# If these install, restart the kernal so it has access to the recently installed files

In [ ]:
!pip3 install --user transformers datasets evaluate rouge_score
!pip3 install --user datasets
!pip install --user transformers[torch]
!pip install --user accelerate -U
!pip install --user wandb

# Logging into huggingface hub

In [1]:
from huggingface_hub import notebook_login

notebook_login()

# Naming the WANDB project and notebook

In [2]:
# Must set the global variable WANDB_NOTEBOOK_NAME to the name of the notebook
import os
import wandb
# Name is found through the os incase the name changes
# WANDB_NOTEBOOK_NAME = os.path.basename(os.getcwd())
notebook_name = str(os.path.basename(os.getcwd()))
os.environ["WANDB_NOTEBOOK_NAME"] = "./" + notebook_name
os.environ["WANDB_PROJECT"] = "congress_bill_summary_model"
wandb.init(project='congress_bill_sumamry_model') 

wandb: WARNING WANDB_NOTEBOOK_NAME should be a path to a notebook file, couldn't find ./TermProject.
wandb: Currently logged in as: tah6k (cheaptrix). Use `wandb login --relogin` to force relogin


# Importing and loading the Congressional Bills dataset

In [3]:
import datasets
from datasets import load_dataset
import pandas as pd
from datasets import Dataset
import json

# Opening JSON file
with open("cleaned_bill_sum_data.json") as json_file:
    cleaned_data = json.load(json_file)
data = pd.DataFrame.from_dict(cleaned_data)
dataset = Dataset.from_pandas(pd.DataFrame(data=data))

# Splitting the data to training and testing split

In [4]:
billsum = dataset.train_test_split(test_size=0.2)

# Example of data within the training set

In [5]:
billsum["train"][0]

{'summary': '(This measure has not been amended since it was introduced. The summary of that version is repeated here.) Declares that when the House adjourns on any legislative day from Friday, July 15, 2016, through Friday, September 2, 2016, it stand adjourned until 2 p.m. on Tuesday, September 6, 2016.',
 'text': 'A concurrent resolution providing for an adjournment of the House of Representatives. 2016-07-14 Passed Senate without amendment (This measure has not been amended since it was introduced. The summary of that version is repeated here.) Declares that when the House adjourns on any legislative day from Friday, July 15, 2016, through Friday, September 2, 2016, it stand adjourned until 2 p.m. on Tuesday, September 6, 2016. 2016-07-14 Introduced in Senate Declares that when the House adjourns on any legislative day from Friday, July 15, 2016, through Friday, September 2, 2016, it stand adjourned until 2 p.m. on Tuesday, September 6, 2016. text/xml EN Pursuant to Title 17 Sectio

# Load T5 tokenizer to process text and summary

In [6]:
from transformers import AutoTokenizer

checkpoint = "google-t5/t5-small"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)

# Perprocessing Function

In [7]:
prefix = "summarize: "


def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    labels = tokenizer(text_target=examples["summary"], max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

# Tokenize the dataset using the map function

In [8]:
tokenized_billsum = billsum.map(preprocess_function, batched=True)

Map:   0%|          | 0/212 [00:00<?, ? examples/s]

Map:   0%|          | 0/53 [00:00<?, ? examples/s]

# Creating a batch of examples using DataCollatorForSeq2Seq with dynamic padding

In [9]:
from transformers import DataCollatorForSeq2Seq

data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=checkpoint)

2024-04-12 23:20:17.382485: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-04-12 23:20:17.422130: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-04-12 23:20:17.422161: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-04-12 23:20:17.422185: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-04-12 23:20:17.429463: I tensorflow/core/platform/cpu_feature_g

# Importing the evaluator

In [10]:
import evaluate

rouge = evaluate.load("rouge")

# Function that passes predictions and labels to compute to calculate the Rouge metric.

In [11]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    result = rouge.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)

    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in predictions]
    result["gen_len"] = np.mean(prediction_lens)

    return {k: round(v, 4) for k, v in result.items()}

# Training - Loading T5 with AutoModelForSeq2SeqLM

In [12]:
from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer

model = AutoModelForSeq2SeqLM.from_pretrained(checkpoint)

# Defining the training hyperparameters

In [13]:
# ORIGINAL
# training_args = Seq2SeqTrainingArguments(
#     output_dir="my_awesome_billsum_model",
#     evaluation_strategy="epoch",
#     learning_rate=2e-5,
#     per_device_train_batch_size=16,
#     per_device_eval_batch_size=16,
#     weight_decay=0.01,
#     save_total_limit=3,
#     num_train_epochs=4,
#     predict_with_generate=True,
#     fp16=True,
#     push_to_hub=True,
# )

training_args = Seq2SeqTrainingArguments(
    output_dir="congress_bill_summary_model",
    evaluation_strategy="epoch",
    learning_rate=2e-4,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=4,
    predict_with_generate=True,
    fp16=True,
    push_to_hub=True,
)

# Passing the arguments, model, dataset, tokenizer, data collator, and compute_metrics function to Seq2SeqTrainer for training

In [14]:
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_billsum["train"],
    eval_dataset=tokenized_billsum["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

/home/u.th161689/.local/lib/python3.11/site-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False)
  warnings.warn(
Detected kernel version 4.18.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


# Fine-tuning the model

In [15]:
# Training needs numpy
import numpy as np

# Fine-tuning the model
trainer.train()

You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


/opt/conda/lib/python3.11/site-packages/transformers/generation/utils.py:1355: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


TrainOutput(global_step=56, training_loss=0.17396153722490584, metrics={'train_runtime': 39.9457, 'train_samples_per_second': 21.229, 'train_steps_per_second': 1.402, 'total_flos': 177655146872832.0, 'train_loss': 0.17396153722490584, 'epoch': 4.0})

# Saving the Model

In [16]:
trainer.save_model("./congress_bill_summary_model")

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

events.out.tfevents.1712982022.fc003.3364345.0:   0%|          | 0.00/7.79k [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/4.86k [00:00<?, ?B/s]

events.out.tfevents.1712981439.fc003.3322740.0:   0%|          | 0.00/7.79k [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

# Pushing Model to Personal HuggingFace Hub

In [17]:
trainer.push_to_hub("cheaptrix/congress_bill_summary_model")

CommitInfo(commit_url='https://huggingface.co/cheaptrix/congress_bill_summary_model/commit/dcdfc898778d0665ae87f330cd063a2a27fee3f4', commit_message='cheaptrix/congress_bill_summary_model', commit_description='', oid='dcdfc898778d0665ae87f330cd063a2a27fee3f4', pr_url=None, pr_revision=None, pr_num=None)

# Interface

In [18]:
cleaned_test_data = []
# Opening JSON file
with open("cleaned_bill_sum_test_data.json") as json_file:
    cleaned_test_data = json.load(json_file)

# Creating a pipeline with the transformers module

In [19]:
from transformers import pipeline

summarizer = pipeline("summarization", model="cheaptrix/congress_bill_summary_model")

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

In [20]:
text = cleaned_test_data[3]['text']
text

'A concurrent resolution establishing deadlines for the Joint Committee of Congress on the Library to approve or deny the statue of the Reverend William Franklin "Billy" Graham, Jr., for placement in the National Statuary Hall. 2023-02-16 Introduced in Senate This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham for placement in the National Statuary Hall within 30 days after North Carolina submits specific information about the statute, including its dimensions and final weight. text/xml EN Pursuant to Title 17 Section 105 of the United States Code, this file is not subject to copyright protection and is in the public domain. Congressional Research Service, Library of Congress This file contains bill summaries for federal legislation. A bill summary describes the most significant provisions of a piece of legislation and details the effects the legislative text may have on current law and federal programs. Bill summari

In [21]:
summarizer(text)

[{'summary_text': 'This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham for placement in the National Statuary Hall within 30 days after North Carolina submits specific information about the statute, including its dimensions and final weight.'}]

In [22]:
cleaned_test_data[3]['summary']

'This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham for placement in the National Statuary Hall within 30 days after North Carolina submits specific information about the statute, including its dimensions and final weight.'

In [23]:
generated_summaries = []
for i in range(len(cleaned_test_data)):
    summary = summarizer(cleaned_test_data[i]['text'])
    generated_summaries.append({"generated" : summary[0]['summary_text'], "summary" : cleaned_test_data[i]['summary']})

Token indices sequence length is longer than the specified maximum sequence length for this model (548 > 512). Running this sequence through the model will result in indexing errors


In [24]:
generated_summaries[0]

{'generated': 'This resolution requires the Architect of the Capitol, the Secretary of the Senate, and the Chief Administrative Officer of the House of Representatives to encourage Capitol gift shops to accept cryptocurrency and to enter into contracts with vendors that accept cryptocurrency to provide food service and vending machines in the Capitol.',
 'summary': 'Adopting Cryptocurrency in Congress as an Exchange of Payment for Transactions Resolution or the ACCEPT Resolution This resolution requires the Architect of the Capitol, the Secretary of the Senate, and the Chief Administrative Officer of the House of Representatives to encourage Capitol gift shops to accept cryptocurrency and to enter into contracts with vendors that accept cryptocurrency to provide food service and vending machines in the Capitol.'}

In [25]:
generated_summaries[1]

{'generated': 'This concurrent resolution commends the bravery, courage, and resolve of the women and men of Iran who are (1) participating in the current protests to defend their fundamental human rights, and (2) risking their safety to speak out against the human rights abuses committed by the Iranian regime.',
 'summary': 'This concurrent resolution commends the bravery, courage, and resolve of the women and men of Iran who are (1) participating in the current protests to defend their fundamental human rights, and (2) risking their safety to speak out against the human rights abuses committed by the Iranian regime. The resolution condemns (1) the brutal beating and death of Mahsa Amini; and (2) the violent suppression by the Iranian regime of women and men participating in the current demonstrations, including children, and calls for transparent accountability for all killings of protesters by Iranian security forces. Finally, the resolution encourages continued efforts by the Biden

In [26]:
generated_summaries[2]

{'generated': 'This concurrent resolution calls for honoring the 237th anniversary of the enactment of the Virginia Statute for Religious Freedom on Religious Freedom Day, January 16, 2023. The resolution affirms that religious freedom includes the right of individuals of any faith and individuals of no faith to live, work, associate, and worship in accordance with their beliefs; all people of the United States can be unified in supporting religious freedom because it is a fundamental human right; and the American people will remain forever unshackled in matters of faith.',
 'summary': 'This concurrent resolution calls for honoring the 237th anniversary of the enactment of the Virginia Statute for Religious Freedom on Religious Freedom Day, January 16, 2023. The resolution affirms that religious freedom includes the right of individuals of any faith and individuals of no faith to live, work, associate, and worship in accordance with their beliefs; all people of the United States can be

In [27]:
generated_summaries[3]

{'generated': 'This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham for placement in the National Statuary Hall within 30 days after North Carolina submits specific information about the statute, including its dimensions and final weight.',
 'summary': 'This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham for placement in the National Statuary Hall within 30 days after North Carolina submits specific information about the statute, including its dimensions and final weight.'}

In [28]:
generated_summaries[4]

{'generated': 'This concurrent resolution declares that Congress should not impose any new performance fee, tax, royalty, or other charge relating to the public performance of sound recordings on a local radio station for broadcasting sound recordings over the air or on any business for such public performance .',
 'summary': 'This concurrent resolution declares that Congress should not impose any new performance fee, tax, royalty, or other charge relating to the public performance of sound recordings on a local radio station for broadcasting sound recordings over the air or on any business for such public performance of sound recordings.'}

In [29]:
generated_summaries[5]

{'generated': 'This concurrent resolution recognizes Abortion Provider Appreciation Day. Text/xml EN Pursuant to Title 17 Section 105 of the United States Code, this file is not subject to copyright protection and is in the public domain.',
 'summary': 'This concurrent resolution recognizes Abortion Provider Appreciation Day.'}

In [30]:
generated_summaries[6]

{'generated': "This concurrent resolution condemns Russia's unjust and arbitrary detention of Russian democratic opposition leader Vladimir Kara-Murza and calls for his immediate release and the release of all other Russian opposition leaders.",
 'summary': "This concurrent resolution condemns Russia's unjust and arbitrary detention of Russian democratic opposition leader Vladimir Kara-Murza and calls for his immediate release and the release of all other Russian opposition leaders. It also calls for the release of all political prisoners in Russia and in Belarus, as well as for the release of Ukrainian citizens held by Russia, and calls on the President and leaders of the free world to work tirelessly for the release of political prisoners in Russia."}

In [31]:
generated_summaries[7]

{'generated': 'This concurrent resolution expresses the sense of Congress that tax-exempt fraternal benefit societies provide critical benefits to the people and communities of the United States and their work should continue to be promoted.',
 'summary': 'This concurrent resolution expresses the sense of Congress that tax-exempt fraternal benefit societies provide critical benefits to the people and communities of the United States and their work should continue to be promoted.'}

In [32]:
generated_summaries[8]

{'generated': 'This concurrent resolution expresses the sense of Congress that climate change caused by human activities constitutes a climate emergency, which demands the President use existing authorities and emergency powers to mitigate and prepare for the consequences of the emergency.',
 'summary': 'This concurrent resolution expresses the sense of Congress that climate change caused by human activities constitutes a climate emergency, which demands the President use existing authorities and emergency powers to mitigate and prepare for the consequences of the emergency.'}

In [33]:
generated_summaries[9]

{'generated': "Fiscal State of the Nation Resolution This concurrent resolution requires the congressional budget committees to conduct an annual joint hearing to receive a presentation from the Comptroller General regarding (1) the Government Accountability Office's audit of the financial statement of the executive branch, and (2) the financial position and condition of the federal government.",
 'summary': "Fiscal State of the Nation Resolution This concurrent resolution requires the congressional budget committees to conduct an annual joint hearing to receive a presentation from the Comptroller General regarding (1) the Government Accountability Office's audit of the financial statement of the executive branch, and (2) the financial position and condition of the federal government."}

In [34]:
generated_summaries[10]

{'generated': 'This concurrent resolution expresses the sense that the Senate should provide its advice and consent to ratification of the Convention on Biological Diversity.',
 'summary': 'This concurrent resolution expresses the sense that the Senate should provide its advice and consent to ratification of the Convention on Biological Diversity.'}

In [35]:
generated_summaries[11]

{'generated': 'This concurrent resolution calls on the media to voluntarily adopt certain practices to prevent further harm from its coverage of mass public murders. Specifically, it calls for coverage that (1) denies murderers a public platform; (2) minimizes the potential for media reporting to increase the likelihood of future mass public killings (i.e., the media contagion effect); and (3) prioritizes the victims of, and heroism in the response to, mass public killers.',
 'summary': 'This concurrent resolution calls on the media to voluntarily adopt certain practices to prevent further harm from its coverage of mass public murders. Specifically, it calls for coverage that (1) denies murderers a public platform; (2) minimizes the potential for media reporting to increase the likelihood of future mass public murders (i.e., the media contagion effect); and (3) prioritizes the victims of, and heroism in the response to, mass public murders.'}

In [36]:
generated_summaries[12]

{'generated': 'This concurrent resolution affirms, more than 400 years after the arrival of the first slave ship, that the United States owes a debt of remembrance to those who lived through slavery or other historical injustices against people of color, as well as to their descendants. It also urges the establishment of a U.S. Commission on Truth, Racial Healing, and Transformation',
 'summary': 'This concurrent resolution affirms, more than 400 years after the arrival of the first slave ship, that the United States owes a debt of remembrance to those who lived through slavery or other historical injustices against people of color, as well as to their descendants. It also urges the establishment of a U.S. Commission on Truth, Racial Healing, and Transformation.'}

In [37]:
generated_summaries[13]

{'generated': "This concurrent resolution recognizes the disparity between wages paid to Latina women in comparison to men and reaffirms Congress's support for ensuring equal pay and closing the gender wage gap.",
 'summary': "This concurrent resolution recognizes the disparity between wages paid to Latina women in comparison to men and reaffirms Congress's support for ensuring equal pay and closing the gender wage gap."}

In [38]:
generated_summaries[14]

{'generated': 'This concurrent resolution expresses the sense of Congress that a carbon tax would be detrimental to families and businesses and would severely harm the economic and national security of the country.',
 'summary': 'This concurrent resolution expresses the sense of Congress that a carbon tax would be detrimental to families and businesses and would severely harm the economic and national security of the country.'}

In [39]:
generated_summaries[15]

{'generated': 'This concurrent resolution makes a correction to the official title of H.R. 815 (Making emergency supplemental appropriations for the fiscal year ending September 30, 2024, and for other purposes).',
 'summary': 'This concurrent resolution makes a correction to the official title of H.R. 815 (Making emergency supplemental appropriations for the fiscal year ending September 30, 2024, and for other purposes).'}

In [40]:
new_cleaned_test_data = []
# Opening JSON file
with open("new_cleaned_bill_sum_test_data.json") as json_file:
    new_cleaned_test_data = json.load(json_file)

In [41]:
new_cleaned_test_data

[{'summary': 'Saving Access to Laboratory Services Act This bill modifies provisions relating to Medicare payment rates for clinical diagnostic laboratory services, including by requiring payment rates for certain widely available clinical diagnostic laboratory tests to be based on a statistical sampling of private sector rates.',
  'text': 'Saving Access to Laboratory Services Act 2023-03-28 Introduced in Senate Saving Access to Laboratory Services Act This bill modifies provisions relating to Medicare payment rates for clinical diagnostic laboratory services, including by requiring payment rates for certain widely available clinical diagnostic laboratory tests to be based on a statistical sampling of private sector rates. text/xml EN Pursuant to Title 17 Section 105 of the United States Code, this file is not subject to copyright protection and is in the public domain. Congressional Research Service, Library of Congress This file contains bill summaries for federal legislation. A bil

In [42]:
new_generated_summaries = []
for i in range(len(new_cleaned_test_data)):
    summary = summarizer(new_cleaned_test_data[i]['text'])
    new_generated_summaries.append({"generated" : summary[0]['summary_text'], "summary" : new_cleaned_test_data[i]['summary']})

In [43]:
new_generated_summaries[0]

{'generated': 'Saving Access to Laboratory Services Act This bill modifies provisions relating to Medicare payment rates for clinical diagnostic laboratory services, including by requiring payments rates for certain widely available clinical diagnostic lab tests to be based on a statistical sampling of private sector rates.',
 'summary': 'Saving Access to Laboratory Services Act This bill modifies provisions relating to Medicare payment rates for clinical diagnostic laboratory services, including by requiring payment rates for certain widely available clinical diagnostic laboratory tests to be based on a statistical sampling of private sector rates.'}

In [44]:
new_generated_summaries[1]

{'generated': 'USDA must periodically review and revise the plan, as necessary, and annually report on its implementation. Additionally, the bill expands the scope of various USDA research, extension, and education programs; conservation programs; and livestock programs to incorporate climate change adaptation and mitigation. Expanded activities include efforts to improve soil health and preserve farmland and grassland. Further, the Bill changes programs that support renewable energy in rural areas to address carbon emissions in the agriculture sector.',
 'summary': 'Agriculture Resilience Act of 2023 This bill establishes, expands, and revises multiple programs and activities of the Department of Agriculture (USDA) primarily to reduce carbon emissions from the agriculture sector. Specifically, USDA must finalize and implement a plan to achieve net-zero emissions from the sector by 2040. USDA must periodically review and revise the plan, as necessary, and annually report on its impleme